<center> <img src = https://raw.githubusercontent.com/AndreyRysistov/DatasetsForPandas/main/hh%20label.jpg alt="drawing" style="width:400px;">

# <center> Проект: Анализ вакансий из HeadHunter
   

In [76]:
import pandas as pd
import psycopg2
import plotly.express as px
from PIL import Image
import requests # Импортируем библиотеку requests
from bs4 import BeautifulSoup
import warnings

In [77]:
# вставьте сюда параметры подключения из юнита 1. Работа с базой данных из Python 
# ДАННЫЕ СОЕДИНЕНИЯ УДАЛЕНЫ.

In [78]:
connection = psycopg2.connect(
    dbname=DBNAME,
    user=USER,
    host=HOST,
    password=PASSWORD,
    port=PORT
)
warnings.filterwarnings('ignore', message = '.*SQLAlchemy connectable')

# Юнит 3. Предварительный анализ данных

1. Напишите запрос, который посчитает количество вакансий в нашей базе (вакансии находятся в таблице vacancies). 

In [79]:
# текст запроса
query_3_1 = f'''
SELECT 
    COUNT(*) cnt_vacancies
FROM
    public.vacancies v
'''

In [80]:
# результат запроса
# используем метод read_sql_query, чтобы получить результаты запроса 
df = pd.read_sql_query(query_3_1, connection)
display(df)

cnt_vacancies
0          49197

2. Напишите запрос, который посчитает количество работодателей (таблица employers). 

In [81]:
# текст запроса
query_3_2 = f'''
SELECT 
    COUNT(*) cnt_employers
FROM
    public.employers e
'''

In [82]:
# результат запроса
df = pd.read_sql_query(query_3_2, connection)
display(df)

cnt_employers
0          23501

3. Посчитате с помощью запроса количество регионов (таблица areas).

In [83]:
# текст запроса
query_3_3 = f'''
SELECT
    COUNT(*) cnt_areas
FROM 
    public.areas a
'''

In [84]:
# результат запроса
df = pd.read_sql_query(query_3_3, connection)
display(df)

cnt_areas
0       1362

4. Посчитате с помощью запроса количество сфер деятельности в базе (таблица industries).

In [85]:
# текст запроса
query_3_4 = f'''
SELECT
    COUNT(*) cnt_industries
FROM 
    public.industries i
    '''

In [86]:
# результат запроса
df = pd.read_sql_query(query_3_4, connection)
display(df)

cnt_industries
0             294

***

In [87]:
# выводы по предварительному анализу данных

## выводы по предварительному анализу данных
1. Компания HeadHunter имеет обширную базу данных вакансий IT-специалистов, которых она может подобрать IT компаниям. В базе данных всего представдено 294 сфер деятельности, в 1362 регионах. 23501 работодателей ищет себе специалистов, на 49197 вакансий. База имеет значимую выборку на которой можно строить различные модели машинного обучения. В частности модель, которая будет рекомендовать вакансии клиентам агентства, претендующим на позицию Data Scientist. Вывод по предварительному анализу данных (Data Understanding): Данные соответствуют целям проекта — создание модели машинного обучения, которая будет рекомендовать вакансии клиентам агентства, претендующим на позицию Data Scientist.

# Юнит 4. Детальный анализ вакансий

1. Напишите запрос, который позволит узнать, сколько (cnt) вакансий в каждом регионе (area).
Отсортируйте по количеству вакансий в порядке убывания.

In [88]:
# текст запроса
query_4_1 = f'''
SELECT
    a.name area,
    COUNT(v.id) cnt_vacancies
FROM
    public.vacancies v
JOIN public.areas a ON v.area_id = a.id --INNER JOIN т.е вакансии, где не указан регион отбрасываем
GROUP BY a.name
ORDER BY COUNT(v.id) DESC
LIMIT 5
'''

In [89]:
# результат запроса
df = pd.read_sql_query(query_4_1, connection)
display(df)

area  cnt_vacancies
0           Москва           5333
1  Санкт-Петербург           2851
2            Минск           2112
3      Новосибирск           2006
4           Алматы           1892

2. Напишите запрос, чтобы определить у какого количества вакансий заполнено хотя бы одно из двух полей с зарплатой.

In [90]:
# текст запроса
query_4_2 = f'''
SELECT
    COUNT(*) cnt_vac_with_salary
FROM
    public.vacancies v
WHERE
    v.salary_from IS NOT null OR v.salary_to IS NOT null
'''

In [91]:
# результат запроса
df = pd.read_sql_query(query_4_2, connection)
display(df)

cnt_vac_with_salary
0                24073

3. Найдите средние значения для нижней и верхней границы зарплатной вилки. Округлите значения до целого.

In [92]:
# текст запроса
query_4_3 = f'''
SELECT
    ROUND(AVG(salary_from)) avg_salary_from,
    ROUND(AVG(salary_to)) avg_salary_to
FROM public.vacancies v
'''

In [93]:
# результат запроса
df = pd.read_sql_query(query_4_3, connection)
display(df)

avg_salary_from  avg_salary_to
0          71065.0       110537.0

4. Напишите запрос, который выведет количество вакансий для каждого сочетания типа рабочего графика (schedule) и типа трудоустройства (employment), используемого в вакансиях. Результат отсортируйте по убыванию количества.


In [94]:
# текст запроса
# группировка по двум признакам дает сочетание этих признаков при выводе.
query_4_4 = f'''
SELECT 
    v.schedule schedule, 
    v.employment employment, 
    COUNT(*) AS vacancies_cnt
FROM 
    public.vacancies v
GROUP BY 
    v.schedule, 
    v.employment
ORDER BY 
    vacancies_cnt DESC
LIMIT 20
'''

In [95]:
# результат запроса
df = pd.read_sql_query(query_4_4, connection)
display(df)

schedule           employment  vacancies_cnt
0        Полный день     Полная занятость          35367
1   Удаленная работа     Полная занятость           7802
2      Гибкий график     Полная занятость           1593
3   Удаленная работа  Частичная занятость           1312
4     Сменный график     Полная занятость            940
5        Полный день           Стажировка            569
6     Вахтовый метод     Полная занятость            367
7        Полный день  Частичная занятость            347
8      Гибкий график  Частичная занятость            312
9        Полный день     Проектная работа            141
10  Удаленная работа     Проектная работа            133
11     Гибкий график           Стажировка            116
12    Сменный график  Частичная занятость            101
13  Удаленная работа           Стажировка             64
14     Гибкий график     Проектная работа             18
15    Сменный график           Стажировка             12
16    Вахтовый метод     Проектная работа              2
17    Сменный график     Проектная работа              1

In [96]:
fig=px.density_heatmap(
    df,
    x='schedule',
    y='employment',
    z='vacancies_cnt',
    title='К-во вакансий для сочетаний типа рабочего графика (schedule) и типа трудоустройства (employment)'
    )
fig.show()
#fig.write_image('images/img1.png')     # если граффик не появился (в GIT, например) покажем его как предварительно сохраненную копию
img=Image.open('images/img1.png')
img.show()

[дополнительная ссылка на текущий график](images/img1.png 'img1.png')

![дополнительная ссылка на текущий график](images/img1.png 'img1.png')

5. Напишите запрос, выводящий значения поля Требуемый опыт работы (experience) в порядке возрастания количества вакансий, в которых указан данный вариант опыта. 

In [97]:
# текст запроса
query_4_5 = f'''
SELECT 
    v.experience experience, 
    COUNT(*) AS vacancies_cnt
FROM 
    public.vacancies v
GROUP BY 
    1
ORDER BY 
    vacancies_cnt ASC;
'''

In [98]:
# результат запроса
df = pd.read_sql_query(query_4_5, connection)
display(df)

experience  vacancies_cnt
0         Более 6 лет           1337
1           Нет опыта           7197
2       От 3 до 6 лет          14511
3  От 1 года до 3 лет          26152

In [99]:
#hh_less_1m_grpd = hh_df.where(hh_df['ЗП (руб)'] < 1000000).groupby('Образование', as_index=False)['ЗП (руб)'].median()
fig = px.bar(
    df,
    y='vacancies_cnt',
    x='experience',
    title='Зависимость К-ва предлагаемых вакансий от  Требуемого опыта работы',
    width=1000,      
    height= 500
    )
fig.show()   # покажем интерактивный график
#fig.write_image('images/img2.png')     # если граффик не появился (в GIT, например) покажем его как предварительно сохраненную копию
img=Image.open('images/img2.png')
img.show()

[дополнительная ссылка на текущий график](images/img2.png 'img2.png')

![дополнительная ссылка на текущий график](images/img2.png 'img2.png')

***

In [100]:
# выводы по детальному анализу вакансий

### выводы по детальному анализу вакансий.
1. Вакансии по регионам. Москва безспорный лидер по к-ву предлагаемых вакансий- 5333, это почти вдвое больше, чем у второго по к-ву вакансий региона - Санкт-Петербургу(2851). К-во выкансий у других регионов из пятерки лидеров зависит в меньшей степени от конкретного региона.
2. В базе много записей с незаполненными значениями запрашиваемой нижней или верхней границы зарплат (24073), протоив 49197- всего вакансий. Будет необходимо принимать решение, как заполнять эти пропуски. Средние значения зарплат по всем вакансиям находятся в диапазоне (71065-111537р). Я думаю эти цифры сильно усредненные, медианные значения зарплат с разбивкой по опыту и ключевым навыкам могут дать данные точнее.
3. К-во вакансий в зависимости от сочетания графика работы (schedule) и вида занятости (employement) показали, что самое распространенное сочетание ПолныйДень-ПолнаяЗанятость (35367), на втором месте УдаленнаяРабота- ПолнаяЗанятость (7802)- разница более, чем в 4.5 раза (на hetmap это видно наличем желтого цвета в нижнем левом углу и синего цвета по всей диаграмме). К тому же УдаленнаяРабота, с высокой вероятностью это наследие времен пандемии Covid-19. Вывод: ПолныйДень-ПолнаяЗанятость абсолютный лидер в разбивке по графику работы (schedule) и виду занятости(employement).
4. Опыт работы показывает что самая многочисленная категория 1-3 года. То есть много вакансий для людей с опытом до 3х лет. На столбчатой диаграмме это представленно наглядно. Стоит отметить, что специалисты без опыта так же требуются, что дает возможность успешного старта для новичков.

# Юнит 5. Анализ работодателей

1. Напишите запрос, который позволит узнать, какие работодатели находятся на первом и пятом месте по количеству вакансий.

In [101]:
# текст запроса
# два запроса объединяются UNIT ALL, только чтобы вывести по 1 значению не подряд
query_5_1 = f'''
(
SELECT
    e.name employer,
    COUNT(v.id) cnt_vacancies
FROM
    public.vacancies v
JOIN 
    public.employers e ON v.employer_id = e.id
GROUP BY v.employer_id, e.name
ORDER BY cnt_vacancies DESC
LIMIT 1
)
UNION ALL
(
SELECT
    e.name,
    COUNT(v.id)
FROM
    public.vacancies v
JOIN
    public.employers e ON v.employer_id = e.id
GROUP BY v.employer_id, e.name
ORDER BY 2 DESC
OFFSET 4
LIMIT 1
)
'''

In [102]:
# результат запроса
df = pd.read_sql_query(query_5_1, connection)
display(df)

employer  cnt_vacancies
0         Яндекс           1933
1  Газпром нефть            331

2. Напишите запрос, который для каждого региона выведет количество работодателей и вакансий в нём.
Среди регионов, в которых нет вакансий, найдите тот, в котором наибольшее количество работодателей.


In [103]:
# текст запроса
query_5_2 = f'''
SELECT
    a.name area,
    COUNT(DISTINCT e.id) num_empl,
    COUNT(v.id) num_vacan
FROM
    public.areas a
LEFT JOIN public.employers e ON a.id = e.area     --LEFT JOIN- оставляем не совпадающие записи с NULL
LEFT JOIN public.vacancies v ON a.id = v.area_id
WHERE v.area_id IS null
GROUP BY a.id
ORDER BY num_empl DESC
LIMIT 1
'''

In [104]:
# результат запроса
df = pd.read_sql_query(query_5_2, connection)
display(df)

area  num_empl  num_vacan
0  Россия       410          0

3. Для каждого работодателя посчитайте количество регионов, в которых он публикует свои вакансии. Отсортируйте результат по убыванию количества.


In [105]:
# текст запроса
query_5_3 = f'''
SELECT
    e.name employer,
    COUNT(DISTINCT v.area_id) cnt_area
FROM
    public.vacancies v
JOIN 
    public.employers e ON e.id = v.employer_id
GROUP BY e.name
ORDER BY cnt_area DESC
--LIMIT 1
'''

In [106]:
# результат запроса
df = pd.read_sql_query(query_5_3, connection)
display(df)

employer  cnt_area
0                      Яндекс       181
1                  Ростелеком       152
2                  Спецремонт       116
3      Поляков Денис Иванович        88
4                   ООО ЕФИН         71
...                       ...       ...
14761                  UniSol         1
14762            UNISTORY LLC         1
14763                   UNIT6         1
14764     United Distribution         1
14765              UNITEL LLC         1

[14766 rows x 2 columns]

4. Напишите запрос для подсчёта количества работодателей, у которых не указана сфера деятельности. 

In [107]:
# текст запроса
query_5_4 = f'''
SELECT
    COUNT(*) cnt_employers
FROM
    public.employers e
LEFT JOIN
    public.employers_industries ei ON e.id = ei.employer_id
WHERE 
    ei.industry_id IS null
'''

In [108]:
# результат запроса
df = pd.read_sql_query(query_5_4, connection)
display(df)

cnt_employers
0           8419

5. Напишите запрос, чтобы узнать название компании, находящейся на третьем месте в алфавитном списке (по названию) компаний, у которых указано четыре сферы деятельности. 

In [109]:
# текст запроса
query_5_5 = f'''
SELECT
    e.name employer_name,
    COUNT(industry_id) cnt_industries
FROM
    public.employers e
LEFT JOIN
    public.employers_industries ei ON e.id = ei.employer_id
GROUP BY e.name
HAVING COUNT(industry_id) = 4
ORDER BY employer_name
OFFSET 2
LIMIT 1
'''

In [110]:
# результат запроса
df = pd.read_sql_query(query_5_5, connection)
display(df)

employer_name  cnt_industries
0          2ГИС               4

6. С помощью запроса выясните, у какого количества работодателей в качестве сферы деятельности указана Разработка программного обеспечения.


In [111]:
# текст запроса
query_5_6 = f'''
SELECT
    COUNT(*) cnt_employers
FROM
   public.employers_industries ei
JOIN 
    public.industries i ON ei.industry_id = i.id
WHERE
    i.name = 'Разработка программного обеспечения'
'''

In [112]:
# результат запроса
df = pd.read_sql_query(query_5_6, connection)
display(df)

cnt_employers
0           3553

7. Для компании «Яндекс» выведите список регионов-миллионников, в которых представлены вакансии компании, вместе с количеством вакансий в этих регионах. Также добавьте строку Total с общим количеством вакансий компании. Результат отсортируйте по возрастанию количества.

Список городов-милионников надо взять [отсюда](https://ru.wikipedia.org/wiki/%D0%93%D0%BE%D1%80%D0%BE%D0%B4%D0%B0-%D0%BC%D0%B8%D0%BB%D0%BB%D0%B8%D0%BE%D0%BD%D0%B5%D1%80%D1%8B_%D0%A0%D0%BE%D1%81%D1%81%D0%B8%D0%B8). 

Если возникнут трудности с этим задание посмотрите материалы модуля  PYTHON-17. Как получать данные из веб-источников и API. 

In [113]:
# код для получения списка городов-милионников
# Подключаемся к сайту с городами милионниками и получим html текст
url = 'https://ru.wikipedia.org/wiki/%D0%93%D0%BE%D1%80%D0%BE%D0%B4%D0%B0-%D0%BC%D0%B8%D0%BB%D0%BB%D0%B8%D0%BE%D0%BD%D0%B5%D1%80%D1%8B_%D0%A0%D0%BE%D1%81%D1%81%D0%B8%D0%B8' # Определяем значение URL страницы для запроса
response = requests.get(url)
# используем библиотеку BeautifulSoup с параметром html.parser для извлечения нужных тегов
page = BeautifulSoup(response.text, 'html.parser')

list_mln = []  # пустой список для городов
for tag in range(0,16):    # в таблице 16 городов 
    # выбираеим из html тег 'a' стоящий внутри тега 'td'. 
    # Нам нужно таких выборов 16 по количеству городов в первой таблице на сайте
    # берем текст из тега, который соответствует названию города.
    tag_text = page.select('td a')[tag].text
    # текст из тега добавляем в список городов милионников.
    list_mln.append(tag_text)
# преобразуем в кортеж для использования в запросе
list_mln = tuple(list_mln)
#print(list_mln)

# другой способ находим таблицу по class_
# делим строку по title=" на элементы списка и берем элементы, начиная с 4 элемена
# далее каждый элемент списка - строку, делим на элементы другого списка по "> 
# и берем первые элемены, они и есть очередной город, который добавляем в список городов
'''
cities_str = str(page.find('table', class_= 'standard')) 
cities_l = cities_str.split('title="')[3:]
mln_lst=[]
for i in cities_l:
    mln_lst.append(i.split('">')[0])
mln_lst = tuple(mln_lst)
'''


'\ncities_str = str(page.find(\'table\', class_= \'standard\')) \ncities_l = cities_str.split(\'title="\')[3:]\nmln_lst=[]\nfor i in cities_l:\n    mln_lst.append(i.split(\'">\')[0])\nmln_lst = tuple(mln_lst)\n'

In [114]:
# текст запроса
# вторая часть UNION ALL добавляет в вывод столбец 'Total' и общее к-во вакансий Яндекс по всем городам
query_5_7 = f'''
SELECT
    a.name AS area_name, 
    COUNT(v.id) cnt_vacancies
FROM 
    public.vacancies v
JOIN
    public.employers e ON v.employer_id = e.id
JOIN 
    public.areas a ON v.area_id = a.id
WHERE   e.name = 'Яндекс'
        AND a.name IN {list_mln}
GROUP BY a.name
UNION ALL
SELECT
    'Total',
    COUNT(v.id)
FROM 
    public.vacancies v
JOIN
    public.employers e ON v.employer_id = e.id
JOIN 
    public.areas a ON v.area_id = a.id
WHERE e.name = 'Яндекс'
    AND a.name IN {list_mln}
ORDER BY cnt_vacancies
'''

In [115]:
# результат запроса
df = pd.read_sql_query(query_5_7, connection)
display(df)

area_name  cnt_vacancies
0              Омск             21
1         Челябинск             22
2        Красноярск             23
3         Волгоград             24
4             Пермь             25
5            Казань             25
6    Ростов-на-Дону             25
7               Уфа             26
8            Самара             26
9         Краснодар             30
10          Воронеж             32
11      Новосибирск             35
12  Нижний Новгород             36
13     Екатеринбург             39
14  Санкт-Петербург             42
15           Москва             54
16            Total            485

***

In [116]:
# выводы по анализу работодателей

### Выводы по анализу работодателей.
Анализ работодателей, показал, что пятерка компаний с наибольшим числом вакансий следующая:
- Яндекс 1933 вакансий
- Ростелеком 491
- Тинькофф 444
- Сбер 428
- Газпром нефть 321

Итак, абсолютный лидер Яндекс, причем с опережением почти в 4 раза ближайшего соседа - Ростелеком. Это доказывает, что Яндекс является крурнейшей IT компанией на территорииях, где работает HH. 

Сбер с её огромной клиентской сетью на территории СНГ и в часности Рссии только на четвертом месте, уступив Тинькофф.

Россия среди регионов занимает лидирующее место по числу работодателей, даже если у этих работодателей нет текущих соответствующих вакансий, это работает на возможный потенциал в будущем.

Яндекс доказал свое лидерство в IT сфере и со стороны присутствия на рынке вакансий в самом большом к-ве регионов - 181. Причем, я бы не сказал, что он присутствует исключительно в крупных городах милионниках, он имеет там 485 вакансий из 1993. Наверное, потому, что IT специалисты- это и специалисты в удаленной работе.

Со стороны сфер деятельности, я бы сказал, что компании в основном сосредоточены на области своей специализации. Только 17% компаний не указала сферу своей деятельности и только 9 компаний из 49197 указала 4 сферы деятельности.

Наряду непосредственно с разработкой программного обеспечения (3553 компании), все больше появляется компаний (23501), которые работают в IT, но занимаются уже прикладными и сервисными задачами, вероятно, уже готовых програмных продуктов.


# Юнит 6. Предметный анализ

1. Сколько вакансий имеет отношение к данным?

Считаем, что вакансия имеет отношение к данным, если в её названии содержатся слова 'data' или 'данн'.

*Подсказка: Обратите внимание, что названия вакансий могут быть написаны в любом регистре.* 


In [117]:
# текст запроса
query_6_1 = f'''
SELECT
    COUNT(*) cnt_vacancies
FROM 
    public.vacancies v
WHERE
    LOWER(v.name) LIKE '%data%' OR LOWER(v.name) LIKE '%данн%'
'''

In [118]:
# результат запроса
df = pd.read_sql_query(query_6_1, connection)
display(df)

cnt_vacancies
0           1771

2. Сколько есть подходящих вакансий для начинающего дата-сайентиста? 
Будем считать вакансиями для дата-сайентистов такие, в названии которых есть хотя бы одно из следующих сочетаний:
* 'data scientist'
* 'data science'
* 'исследователь данных'
* 'ML' (здесь не нужно брать вакансии по HTML)
* 'machine learning'
* 'машинн%обучен%'

** В следующих заданиях мы продолжим работать с вакансиями по этому условию.*

Считаем вакансиями для специалистов уровня Junior следующие:
* в названии есть слово 'junior' *или*
* требуемый опыт — Нет опыта *или*
* тип трудоустройства — Стажировка.
 

In [119]:
# текст запроса
# ILIKE, объединяет функции LIKE и игнорирование регистра
query_6_2 = f'''
SELECT
    COUNT(*) cnt_ds_junior
FROM 
    public.vacancies v
WHERE
    (v.name ILIKE '%data scientist%'
    OR v.name ILIKE '%data science%'
    OR v.name ILIKE '%исследователь данных%'
    OR v.name ILIKE '%ml%' AND v.name NOT ILIKE '%html%'
    OR v.name ILIKE '%machine learning%'
    OR v.name ILIKE '%машинно%бучен%')
    AND (v.name ILIKE '%junior%'
    OR v.experience ILIKE '%нет опыта%'
    OR v.employment ILIKE '%cтажировка%')
'''

In [120]:
# результат запроса
df = pd.read_sql_query(query_6_2, connection)
display(df)

cnt_ds_junior
0             51

3. Сколько есть вакансий для DS, в которых в качестве ключевого навыка указан SQL или postgres?

** Критерии для отнесения вакансии к DS указаны в предыдущем задании.*

In [121]:
# текст запроса
# ILIKE, объединяет функции LIKE и игнорирование регистра
query_6_3 = f'''
SELECT
    COUNT(*) cnt_sql
FROM 
    public.vacancies v
WHERE
    (v.name ILIKE '%data scientist%'
    OR v.name ILIKE '%data science%'
    OR v.name ILIKE '%исследователь данных%'
    OR v.name ILIKE '%ml%' AND v.name NOT ILIKE '%html%'
    OR v.name ILIKE '%machine learning%'
    OR v.name ILIKE '%машинно%бучен%')
    AND (v.key_skills ILIKE '%sql%'
    OR v.key_skills ILIKE '%postgres%')
'''

In [122]:
# результат запроса
df = pd.read_sql_query(query_6_3, connection)
display(df)

cnt_sql
0      229

4. Проверьте, насколько популярен Python в требованиях работодателей к DS.Для этого вычислите количество вакансий, в которых в качестве ключевого навыка указан Python.

** Это можно сделать помощью запроса, аналогичного предыдущему.*

In [123]:
# текст запроса
query_6_4 = f'''
SELECT
    COUNT(*) cnt_py
FROM 
    public.vacancies v
WHERE
    (v.name ILIKE '%data scientist%'
    OR v.name ILIKE '%data science%'
    OR v.name ILIKE '%исследователь данных%'
    OR v.name ILIKE '%ml%' AND v.name NOT ILIKE '%html%'
    OR v.name ILIKE '%machine learning%'
    OR v.name ILIKE '%машинно%бучен%')
    AND v.key_skills ILIKE '%python%'
'''

In [124]:
# результат запроса
df = pd.read_sql_query(query_6_4, connection)
display(df)

cnt_py
0     357

5. Сколько ключевых навыков в среднем указывают в вакансиях для DS?
Ответ округлите до двух знаков после точки-разделителя.

In [125]:
# текст запроса
# Навыки разделены знаком табуляции. Разница длин полной строки и строки без знаков табуляции +1, дает к-во ключевых навыков.
query_6_5 = f'''
SELECT
    round(avg(length(key_skills) - length(replace(key_skills, CHR(9), ''))+1), 2) cnt_key_skills_ds
FROM 
    public.vacancies v
WHERE
    (v.name ILIKE '%data scientist%'
    OR v.name ILIKE '%data science%'
    OR v.name ILIKE '%исследователь данных%'
    OR v.name LIKE '%ML%' AND v.name NOT ILIKE '%html%'
    OR v.name ILIKE '%machine learning%'
    OR v.name ILIKE '%машинно%бучен%')
'''

In [126]:
# результат запроса
df = pd.read_sql_query(query_6_5, connection)
display(df)

cnt_key_skills_ds
0               6.41

6. Напишите запрос, позволяющий вычислить, какую зарплату для DS в **среднем** указывают для каждого типа требуемого опыта (уникальное значение из поля *experience*). 

При решении задачи примите во внимание следующее:
1. Рассматриваем только вакансии, у которых заполнено хотя бы одно из двух полей с зарплатой.
2. Если заполнены оба поля с зарплатой, то считаем зарплату по каждой вакансии как сумму двух полей, делённую на 2. Если заполнено только одно из полей, то его и считаем зарплатой по вакансии.
3. Если в расчётах участвует null, в результате он тоже даст null (посмотрите, что возвращает запрос select 1 + null). Чтобы избежать этой ситуацию, мы воспользуемся функцией [coalesce](https://postgrespro.ru/docs/postgresql/9.5/functions-conditional#functions-coalesce-nvl-ifnull), которая заменит null на значение, которое мы передадим. Например, посмотрите, что возвращает запрос `select 1 + coalesce(null, 0)`

Выясните, на какую зарплату в среднем может рассчитывать дата-сайентист с опытом работы от 3 до 6 лет. Результат округлите до целого числа. 

In [127]:
# фунция COALESCE, возвращает первое не NULL значение. То есть будет выбрано или 2 разных значения, если нет NULL
# или 2 одинаковых не NULL значения, если одна из зарплат NULL
query_6_6 = f'''
SELECT
    v.experience name_exper,
    --round(avg(COALESCE((salary_to + salary_from)/2, v.salary_from, v.salary_to)),0) avg_sal_exper,
    ROUND(AVG((
        COALESCE(v.salary_from, v.salary_to)+COALESCE(v.salary_to, v.salary_from))/2  
        ),0) avg_sal_exper
FROM 
    public.vacancies v
WHERE
    (v.name ILIKE '%data scientist%'
    OR v.name ILIKE '%data science%'
    OR v.name ILIKE '%исследователь данных%'
    OR v.name LIKE '%ML%' AND v.name NOT ILIKE '%html%'
    OR v.name ILIKE '%machine learning%'
    OR v.name ILIKE '%машинн%обучен%')
    AND (v.salary_from IS NOT null OR v.salary_to IS NOT null)
GROUP BY v.experience
'''

In [128]:
# результат запроса
df = pd.read_sql_query(query_6_6, connection)
display(df)

name_exper  avg_sal_exper
0           Нет опыта        74643.0
1  От 1 года до 3 лет       139675.0
2       От 3 до 6 лет       243115.0

***

In [129]:
# выводы по предметному анализу


## Выводы по предметному анализу.
Сегодня специалисты для работы с данными имеют спрос. Всего вакансий такого рода 1771. В том числе для специалистов уровня Junior - 51. Большую роль имееют ключевые навыки, которые имеет кандидат. Например навыки работы с SQL требуются в 229 вакансиях, а с Python в 357. Всего же кандидат для соответствия ожиданиям работодателя должен обладать в среднем 6.41 навыками. И может расчитывать в среднем на зарплату 74643 рубле, даже не имея опыта работа. Уже после первого года работы следует ожидать повышения зарплаты почти вдвое, а после трех лет до уровня выше 240000 рублей.

# Общий вывод по проекту

In [130]:
# подведем итог исследования, обобщите выводы
# здесь можно (это будет плюсом) провести дополнительные исследования данных, сделать прогнозы, продумать варианты продолжения исследования

# Общие выводы.

Были проведены:
- предварительный анализ данных
- детальный анализ вакансий
- анализ работодателей
- предметный анализ требуемых специалистов.
 
Компания HeadHunter обладает уникальной базой данных работодателей, ими требуемых вакансий и потенциальных кандидатов на эти вакансии. Главная цель и идея бизнеса компании- эффективно удовлетворить спрос работодателей на специалистов с предложением специалистами своих опыта, навыков и компетенций.

Считаю, что данные базы данных соответствуют целям проекта — создание модели машинного обучения, которая будет рекомендовать вакансии клиентам агентства, претендующим на позицию Data Scientist, как по объему, так и по качеству наполнения.

Дополнительные исследования требуют данные по нижнему и верхнему уровням зарплат. Это основная мотивация для соискателей принять ту или иную вакансию. Например,

1. Сколько вакансий вообще без указания какой либо зарплаты? Смотри ниже query_4_2_1. Получили 25124- это больше, чем с незаполненными значениями запрашиваемой нижней или верхней границы зарплат (24073). В дальнейшем их надо как то заполнять. Нужно разрабатывать модель, как это делать.
2. Сравнить уровни средних и медианных зарплат. 
    - Вилка средних зарплат (71065-111537р)
    - Вилка медианных зарплат (50000- 80000)   смотри ниже query_4_3_1

Надо решить, как использовать средние и медианные зарплаты в будущей модели. Сейчас видно, что медианные зарпдаты существенно ниже. После обработки пропусков и выбросов надо применять другие методы разведочного анализа (EDA). Сейчас просто построим предварительно пробные диаграммы - гистограммы нижних и верхних границ зарплаты. см. диаграммы ниже после query_4_3_2. Распределения похожи на нормальные распределения с правой ассиметрией и большим к-вом выбросов на верхней границе.

Так же мы узнали, что есть компании с количеством вакансий в разы больше среднего  по рынку, например Яндекс. И есть, например, опыт работы (1-3) года, который больше других требуется. Такие массовые категории следует иметь в виду и по возможности учитывать при построении моделей.

Предметный анализ, я считаю является главной частью исследования для кандидатов на вакансии в особенности. Так как здесь можно найти ответы на ключевые вопросы, а именно- Какие специалисты и навыки востребованны на рынке, сколькими навыками необходимо обладать, чтобы быть успешным в сфере работы с данными.


In [131]:
# текст запроса
query_4_2_1 = f'''
SELECT
    COUNT(*) cnt_vac_without_salary
FROM
    public.vacancies v
WHERE
    v.salary_from IS null AND v.salary_to IS null
'''

In [132]:
df = pd.read_sql_query(query_4_2_1, connection)
display(df)

cnt_vac_without_salary
0                   25124

In [133]:
# Сортируем по зарплате и берем 50 Percentile
query_4_3_1 = f'''
SELECT
    PERCENTILE_CONT(0.5) WITHIN GROUP(ORDER BY v.salary_from) median_sal_from,
    PERCENTILE_CONT(0.5) WITHIN GROUP(ORDER BY v.salary_to) median_sal_to
FROM public.vacancies v
'''

In [134]:
df = pd.read_sql_query(query_4_3_1, connection)
display(df)

median_sal_from  median_sal_to
0          50000.0        80000.0

In [135]:
# Получим таблицу полную vacancies для построения гистограмм зарплаты.
query_4_3_2 = f'''
SELECT
   *
FROM public.vacancies v
'''

In [136]:
df = pd.read_sql_query(query_4_3_2, connection);
#display(df)

In [137]:
fig = px.histogram(
    df, x='salary_from',
    marginal='box',
    title="Распределение по признаку salary_from",
    nbins=50,
     width=1000,      
    height=800
    )   # покажем интерактивный график
fig.show()
#fig.write_image('images/img3.png')     # если граффик не появился (в GIT, например) покажем его как предварительно сохраненную копию
img=Image.open('images/img3.png')
img.show()

[дополнительная ссылка на текущий график](images/img3.png 'img3.png')

<img src=images/img3.png width=1000px height=30%>

In [138]:
fig = px.histogram(
    df, x='salary_to',
    marginal='box',
    title="Распределение по признаку salary_to",
    nbins=50,
     width=1000,      
    height=800
    )   # покажем интерактивный график
fig.show()
#fig.write_image('images/img4.png')     # если граффик не появился (в GIT, например) покажем его как предварительно сохраненную копию
img=Image.open('images/img4.png')
img.show()

[дополнительная ссылка на текущий график](images/img4.png 'img4.png')

![дополнительная ссылка на текущий график](images/img4.png 'img4.png')

In [139]:
# не забываем закрыть соединение после окончания работы
connection.close()